![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Inżynieria uczenia maszynowego </h1>
<h2> 11. <i>Github actions i CML</i>  [laboratoria]</h2> 
<h3> Tomasz Ziętkiewicz (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

## Github actions
<img src="img/expcontrol/github-actions.jpeg">

 - https://docs.github.com/en/actions
 - System ciągłej integracji "wbudowany" w GitHub
 - Darmowy dla publicznych repozytoriów (z większymi niż w płatnych planach [ograniczeniami dotyczącymi zasobów](https://docs.github.com/en/actions/reference/usage-limits-billing-and-administration#usage-limits))
 

https://youtu.be/cP0I9w2coGU

### Terminologia Github Actions
 - *Workflow* - workflow odpowiada "Pipeline" z Jenkinsa.
 - *Job* - workflow składa się z jednego lub kilku "jobs". Każdy z nich może być wykonywany równolegle na innej maszynie (patrz "runner")
 - *Step* - odpowiednik "Stage" z Jenkinsa - służu do grupowania "Actions"
 - *Action* - odpowiednik "Step" z Jenkinsa - pojedyncze polecenie do wykonania, np. dodanie komentarze do Pull requesta, wykonanie polecenia systemowego itp.
 - *Runner* - odpowiednik Jenkinsowego "Agent" - serwer, na którym mogą być wykonywane zadania ("jobs")
   - *Github-hosted runner* - serwer utrzymywany przez Github (2-core CPU, 7 GB RAM, 14 GB SSD). Windows, Linux albo macOS
   - *Self-hosted runner* - nasz własny serwer, z zinstalowaną aplikacją [Github actions runner](https://github.com/actions/runner)
 - *Event* - zdażenie, które odapala ("triggers") uruchomienie Workflow. Np. wypchnięcie zmiany do repozytorium ("push"), utworzenie Pull requesta. [Pełna lista](https://docs.github.com/en/actions/reference/events-that-trigger-workflows)

### Definicja workflow
 - Workflow definiuje się w plikach YAM(o rozszerzeniu `*.yml` albo `*.yaml`) umieszczonych w specjalnym folderze `.github/workflows/` wewnątrz repozytorium
 - Pełna składnia jest opisana [tutaj](https://docs.github.com/en/actions/reference/workflow-syntax-for-github-actions)
 - Podstawowe pola:
   - `name` [opcjonalna] - nazwa, pod którą workflow/step będzie widoczny w UI. Domyślnie ścieżka do pliku yaml
   - `on` - definiuje kiedy workflow ma być odpalony
   - `jobs` - grupuje razem "zadania" do wykonania. Każde może być wykonane na innym "runnerze". Domyślnie wykonywane są równolegle (ale możemy definiować [zależności między jobami](https://docs.github.com/en/actions/reference/workflow-syntax-for-github-actions#jobsjob_idneeds), co powoduje wykonanie ich sekwencyjnie
   - `runs-on` - parametr joba, definujący na jakiej maszynie wirtualnej ma być uruchomiony (np. `ubuntu-latest`)
   - `uses` - umożliwia użycie gotowych akcji zdefiniowanych przez nas, albo przez innych użytkowników, np. `-uses: actions/checkout@v2` spowoduje checkout plików z repozytorium
   - `run` - pozwala uruchomić dowolne ([dostępne/zainstalowane](https://docs.github.com/en/actions/using-github-hosted-runners/about-github-hosted-runners#preinstalled-software)) polecenie, np. `python3 train.py`
   - `env` - pozwala zdefiniować zmienne środowiskowe dostępne dla akcji lub skorzystać ze [zmiennych ustawionych przez Github](https://docs.github.com/en/actions/reference/environment-variables#default-environment-variables)

In [1]:
%cd IUM_11
!mkdir github-actions-hello;\
cd github-actions-hello;\
git init

/home/tomek/AITech/repo/aitech-ium-private/IUM_11
Initialized empty Git repository in /home/tomek/AITech/repo/aitech-ium-private/IUM_11/github-actions-hello/.git/


In [5]:
%cd github-actions-hello
!mkdir -p .github/workflows

/home/tomek/AITech/repo/aitech-ium-private/IUM_11/github-actions-hello


In [6]:
%%writefile .github/workflows/workflow.yml
name: github-actions-hello
on: [push]
jobs:
  hello-job:
    runs-on: ubuntu-latest
    steps:
      - name: Checkout repo
        uses: actions/checkout@v2
      - name: Setup Python
        uses: actions/setup-python@v2.2.2
        with:
            python-version: '3.7'
      - run: python3 --version

Writing .github/workflows/workflow.yml


### Zależności

Maszyny wirtualne ("runners"), na których uruchamiane są "joby" mają zainstalowany zbiór narzędzi. Przykładowa lista dla [Ubuntu 20.04](https://github.com/actions/virtual-environments/blob/main/images/linux/Ubuntu2004-README.md)

Brakujące zależności można zainstalować, korzystając z:
 - akcji
 - poleceń systemowych takich jak `apt install` czy `pip install` uruchomionych poprzez `run`. Patrz [przykład](https://docs.github.com/en/actions/using-github-hosted-runners/customizing-github-hosted-runners#installing-software-on-ubuntu-runners)

### Akcje
Za pomocą polecenia `uses` możemy używać przygotowanych wcześniej akcji. Mogą one pochodzić:
 - z tego samego repozytorium co workflow ([więcej](https://docs.github.com/en/actions/learn-github-actions/finding-and-customizing-actions#referencing-an-action-in-the-same-repository-where-a-workflow-file-uses-the-action))
 - z dowolnego publicznego repozytorium Github (np. [repozytorioum iterative/setup-clm](https://github.com/iterative/setup-cml), patrz przykład poniżej
 - z [Github Marketplace](https://github.com/marketplace?type=actions)

## CML - Continous Machine Learning
<img src="img/expcontrol/cml.png">

 - Tworzone przez [iterative.ai](iterative.ai) (tak jak DVC)
 - https://cml.dev/
 - Dokumentacja: https://dvc.org/doc/cml
 - Korzysta z Github Actions lub Gitlab CI (a także [Bitbucket Pipelines](https://github.com/iterative/cml/wiki/CML-with-Bitbucket-Cloud))
 - CML dodaje do Github Actions kilka "akcji":
   - `iterative/setup-cml` - dodaje poniższe akcje
   - `cml-send-comment` - dodaje raport CML jako komentarz do Pull Requesta na Githubie
   - `cml-send-github-check` - dodaje raport CML do zakładki "Checks" Pull Requesta na Githubie
   - `cml-publish` - umożliwia dodanie obrazka do raportu
   

### Przykładowy Workflow CML:

In [1]:
!git clone git@github.com:TomekZet/example_cml.git

/home/tomek/AITech/repo/aitech-ium-private/IUM_11
Cloning into 'example_cml'...
remote: Enumerating objects: 25, done.
remote: Total 25 (delta 0), reused 0 (delta 0), pack-reused 25
Receiving objects: 100% (25/25), 222.95 KiB | 920.00 KiB/s, done.
Resolving deltas: 100% (6/6), done.


In [5]:
%cd example_cml
!mkdir -p .github/workflows/

/home/tomek/AITech/repo/aitech-ium-private/IUM_11/example_cml


In [14]:
%%writefile .github/workflows/cml.yaml
name: model-training
on: [push]
jobs:
  run:
    runs-on: [ubuntu-latest]
    steps:
      - uses: actions/checkout@v2
      - uses: actions/setup-python@v2
      - uses: iterative/setup-cml@v1
      - name: Train model
        env:
          REPO_TOKEN: ${{ secrets.GITHUB_TOKEN }}
        run: |
          pip install -r requirements.txt
          python train.py

          cat metrics.txt >> report.md
          cml-publish confusion_matrix.png --md >> report.md
          cml-send-comment report.md

Overwriting .github/workflows/cml.yaml


In [ ]:
# %load train.py
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import plot_confusion_matrix
import matplotlib.pyplot as plt
import json
import os
import numpy as np

# Read in data
X_train = np.genfromtxt("data/train_features.csv")
y_train = np.genfromtxt("data/train_labels.csv")
X_test = np.genfromtxt("data/test_features.csv")
y_test = np.genfromtxt("data/test_labels.csv")


# Fit a model
depth = 2
clf = RandomForestClassifier(max_depth=depth)
clf.fit(X_train,y_train)

acc = clf.score(X_test, y_test)
print(acc)
with open("metrics.txt", 'w') as outfile:
        outfile.write("Accuracy: " + str(acc) + "\n")


# Plot it
disp = plot_confusion_matrix(clf, X_test, y_test, normalize='true',cmap=plt.cm.Blues)
plt.savefig('confusion_matrix.png')



Wprowadźmy zmianę do pliku (linijka 17: `depth= = 6`)

In [11]:
%%writefile train.py
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import plot_confusion_matrix
import matplotlib.pyplot as plt
import json
import os
import numpy as np

# Read in data
X_train = np.genfromtxt("data/train_features.csv")
y_train = np.genfromtxt("data/train_labels.csv")
X_test = np.genfromtxt("data/test_features.csv")
y_test = np.genfromtxt("data/test_labels.csv")


# Fit a model
depth = 6
clf = RandomForestClassifier(max_depth=depth)
clf.fit(X_train,y_train)

acc = clf.score(X_test, y_test)
print(acc)
with open("metrics.txt", 'w') as outfile:
        outfile.write("Accuracy: " + str(acc) + "\n")


# Plot it
disp = plot_confusion_matrix(clf, X_test, y_test, normalize='true',cmap=plt.cm.Blues)
plt.savefig('confusion_matrix.png')

Overwriting train.py


Stwórzmy nowy branch "deep_depth":

In [13]:
!git checkout -b deep_depth
!git add train.py .github/workflows/cml.yaml
!git commit -m "Changed depth and added cml workflow"
!git push origin deep_depth

Switched to a new branch 'deep_depth'
[deep_depth 0df0f2c] Changed depth and added cml workflow
 2 files changed, 19 insertions(+), 2 deletions(-)
 create mode 100644 .github/workflows/cml.yaml
Enumerating objects: 8, done.
Counting objects: 100% (8/8), done.
Delta compression using up to 4 threads
Compressing objects: 100% (4/4), done.
Writing objects: 100% (6/6), 738 bytes | 738.00 KiB/s, done.
Total 6 (delta 2), reused 0 (delta 0)
remote: Resolving deltas: 100% (2/2), completed with 2 local objects.
remote: 
remote: Create a pull request for 'deep_depth' on GitHub by visiting:
remote:      https://github.com/TomekZet/example_cml/pull/new/deep_depth
remote: 
To github.com:TomekZet/example_cml.git
 * [new branch]      deep_depth -> deep_depth


<img src="IUM_11/img/github-pr.png">

<img src="IUM_11/img/github-checks.png">

## Zadania
1. Utwórz konto na Github (jeśli jeszcze nie masz)
2. Stwórz publiczne repozytorium. Link do niego wklej do kolumny "Link Github" w arkuszu ["Zapisy na zbiory"](https://teams.microsoft.com/l/file/F62B5988-A797-418D-B085-52E0AF8BD55E?tenantId=73689ee1-b42f-4e25-a5f6-66d1f29bc092&fileType=xlsx&objectUrl=https%3A%2F%2Fuam.sharepoint.com%2Fsites%2F2021SL06-DIUMUI0LABInynieriauczeniamaszynowego-Grupa11%2FShared%20Documents%2FGeneral%2FZapisy%20na%20zbiory.xlsx&baseUrl=https%3A%2F%2Fuam.sharepoint.com%2Fsites%2F2021SL06-DIUMUI0LABInynieriauczeniamaszynowego-Grupa11&serviceName=teams&threadId=19:d67b0dc2ee0849eba517a2aa8507df9c@thread.tacv2&groupId=8cd6b30e-edd9-48db-85ab-259fc11d0c5b) [1 pkt]
2. Stwórz prosty Github workflow wykorzystujący akcje CML, który:
 - zrobi checkout Twojego repozytorium [2 pkt]
 - ściągnie pliki trenujące. Najlepiej byłoby to zrobić za pomocą DVC, ale tym razem uprośćmy zadanie ze względu na koplikacje, które mogą się pojawić przy konfiguracji uwierzytelniania. Pliki można po prostu dodać do repozytorium albo ściągnąć przez wget jeśli są publicznie dostępne [2 pkt]
 - dokona trenowania i ewaluacji [8 pkt]
 - wyniki opublikuje za pomocą `cml-send-github-check` i/lub `cml-send-comment` [2 pkt]